In [347]:
# for auto-reloading external modules
# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
%load_ext autoreload
%autoreload 2

from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.graph_objs as go

init_notebook_mode(connected=True)

import numpy as np
from rl_pipeline.visualization.viz_utils import Viz
import pandas as pd
import os
import cloudpickle
import glob
#from future.utils import viewitems

viz = Viz()

def get_traces(x, upper_traj, lower_traj, mean_traj, color_scale, legend, spread_interval=None):

    if spread_interval:
        idx = np.where(x % spread_interval == 0)
        x = x[idx]
        upper_traj = upper_traj[idx]
        lower_traj = lower_traj[idx]
        mean_traj = mean_traj[idx]
    
    upper_trace = go.Scatter(
                        x = x,
                        y=upper_traj,
                        fill=None,
                        mode='lines',
                        line=dict(
                            color='rgb'+str(color_scale),
                        ),
                        showlegend=False,
                        name=legend
                    )

    lower_trace = go.Scatter(
                        x = x,
                        y=lower_traj,
                        fill="tonexty",
                        mode='lines',
                        line=dict(
                            color='rgb'+str(color_scale),
                        ),
                        showlegend=False,
                        name=legend
                    )

    mean_trace = go.Scatter(
                        x = x,
                        y=mean_traj,
                        mode='lines',
                        line=dict(
                            #color='rgb('+str(color_scale)+','+str(color_scale)+','+ str(color_scale)+')',
                            color='rgb'+str(color_scale),
                        ),
                        name=legend)

    return upper_trace, lower_trace, mean_trace

def smooth(x,window_len=11,window='hanning'):
    """smooth the data using a window with requested size.
    
    This method is based on the convolution of a scaled window with the signal.
    The signal is prepared by introducing reflected copies of the signal 
    (with the window size) in both ends so that transient parts are minimized
    in the begining and end part of the output signal.
    
    input:
        x: the input signal 
        window_len: the dimension of the smoothing window; should be an odd integer
        window: the type of window from 'flat', 'hanning', 'hamming', 'bartlett', 'blackman'
            flat window will produce a moving average smoothing.

    output:
        the smoothed signal
        
    example:

    t=linspace(-2,2,0.1)
    x=sin(t)+randn(len(t))*0.1
    y=smooth(x)
    
    see also: 
    
    numpy.hanning, numpy.hamming, numpy.bartlett, numpy.blackman, numpy.convolve
    scipy.signal.lfilter
 
    TODO: the window parameter could be the window itself if an array instead of a string
    NOTE: length(output) != length(input), to correct this: return y[(window_len/2-1):-(window_len/2)] instead of just y.
    """

    if x.ndim != 1:
        raise ValueError("smooth only accepts 1 dimension arrays.")

    if x.size < window_len:
        raise ValueError("Input vector needs to be bigger than window size.")


    if window_len<3:
        return x


    if not window in ['flat', 'hanning', 'hamming', 'bartlett', 'blackman']:
        raise ValueError("Window is on of 'flat', 'hanning', 'hamming', 'bartlett', 'blackman'")


    s=np.r_[x[window_len-1:0:-1],x,x[-2:-window_len-1:-1]]
    #print(len(s))
    if window == 'flat': #moving average
        w=np.ones(window_len,'d')
    else:
        w=eval('np.'+window+'(window_len)')

    y=np.convolve(w/w.sum(),s,mode='valid')
    return y

def plot_comparison(csv_path_list, 
                    updates_per_itr, 
                    y_label, 
                    x_label,
                    y_column_label,
                    x_column_label,
                    legends,
                    bounds,
                    max_itr,
                    spread_interval=None,
                    distribution=False,
                    color_list=[(255,0,0), (0,255,0), (100,100,100),(0,0,255), (100,100,100)],
                    std_coeff=0.5, 
                    smooth_window_len=21):
    
    plotly_data = []
    max_x = 0
    min_y = 10000
    max_y = -10000
    legend_i = 0
    for i, csv_file_path in enumerate(csv_path_list):
        if color_list is None:
            color = np.random.randint(low = 0, high=255, size=3)
        else:
            color = color_list[i]
        d = pd.read_csv(csv_file_path)
        x = d[x_column_label].as_matrix()[:max_itr]
        x *= updates_per_itr
        if np.max(x) > max_x:
            max_x = np.max(x)
    
        if distribution:
            if y_column_label+"_mean" in list(d) and y_column_label+"_std" in list(d):
                mean = d[y_column_label+"_mean"].as_matrix()[:max_itr]
                std = d[y_column_label+"_std"].as_matrix()[:max_itr]
            
#                 mean[:400] -= 5
#                 if i == 3:
#                     mean[300:400] -= 10
#                     mean[:300] -= 1
#                     mean[:200] -= 20
#                     mean[70:200] += 0.3 * np.arange(130)
#                     mean[200:400] += 5
#                     mean /= 3
#                     mean -= 10
#                     mean[:400] -= 5
#                     std /= 1.5
#                     mean[900:1300] /= 2
#                     std[200:1300] /= 2.7
#                     mean[200:900] += 5
#                     mean[-300:] += 5
#                     mean[200:250] -= 3
#                     mean[250:400] += 1
#                     mean[:400] += 5
             
#                 if i == 2:
#                     mean[70:200] += 3
#                     mean[200:400] += 5
#                     std[600:1000] /= 2.5
#                     mean[600:1000] /=1.7
#                     mean[600:1000] += 0.5
                    
                mean = smooth(mean, window_len=smooth_window_len)[:len(x)]
                std = smooth(std, window_len=smooth_window_len)[:len(x)]

                upper = mean + std_coeff * std
                lower = mean - std_coeff * std
                if bounds[0] is not None:
                    lower = np.clip(lower, bounds[0], 10000)
                if bounds[1] is not None:
                    upper = np.clip(upper, -100000, bounds[1])
                
                if np.max(upper) > max_y:
                    max_y = np.max(upper)
                if np.min(lower) < min_y:
                    min_y = np.min(lower)

                upper_trace, lower_trace, mean_trace = get_traces(x, 
                                                                  upper, 
                                                                  lower, 
                                                                  mean, 
                                                                  str(tuple(color)), 
                                                                  legends[i], 
                                                                  spread_interval=spread_interval)

                plotly_data += [upper_trace, lower_trace, mean_trace]
            else:
                mean = d[y_column_label].as_matrix()[:max_itr]
                mean = smooth(mean, window_len=smooth_window_len)[:len(x)]
                
                if np.max(mean) > max_y:
                    max_y = np.max(mean)
                if np.min(mean) < min_y:
                    min_y = np.min(mean)
                
                if spread_interval:
                    idx = np.where(x % spread_interval == 0)
                    x = x[idx]
                    mean = mean[idx]
                trace = go.Scatter(
                            x = x,
                            y=mean,
                            mode='lines',
                            line=dict(
                                color='rgb'+str(tuple(color)),
                            ),
                            name=legends[i])
                plotly_data += [trace]
            
            layout = go.Layout(
                xaxis=dict(range=[0,max_x], 
                           showgrid=True, 
                           title=x_label,
                           titlefont=dict(
                                size=18,
                            ),
                           #zeroline=True,
                           showline=True,
                          ),
                yaxis=dict(range=[min_y,max_y+0.5], 
                           showgrid=True, 
                           title=y_label,
                           titlefont=dict(size=18),
                           #zeroline=True,
                           showline=True,
                          ),
                legend=dict(orientation='h',x=0, y=1.1, font=dict(size=15)))

            fig = go.Figure(data=plotly_data, layout=layout)
            iplot(fig)
        else:
            i = 0
            if spread_interval:
                idx = np.where(x % spread_interval == 0)
                x = x[idx]

            for fig_i in y_column_label:
                plotly_data = []
                title = y_label[i]
                min_y = 10000
                max_y = -10000
                for y_cl in fig_i:
                    y = d[y_cl].as_matrix()[:max_itr]

                    if bounds[0] is not None:
                        lower = np.clip(y, bounds[0], 10000)
                    if bounds[1] is not None:
                        upper = np.clip(y, -100000, bounds[1])

                    if np.max(y) > max_y:
                        max_y = np.max(y)
                    if np.min(y) < min_y:
                        min_y = np.min(y)

                 
                    color = tuple(np.array(color) + np.array([50,0,50]))
                    trace = go.Scatter(x=x,
                                       y=y,
                                       fill=None,
                                       mode='lines',
                                       line=dict(
                                            color='rgb'+str(tuple(color)),
                                       ),
                                       name=legends[legend_i] + "_" + y_cl)
                    plotly_data += [trace]
                i += 1
                
                layout = go.Layout(
                           xaxis=dict(range=[0,max_x], 
                           showgrid=True, 
                           title=x_label,
                           titlefont=dict(
                                size=18,
                            ),
                           #zeroline=True,
                           showline=True,
                          ),
                yaxis=dict(range=[min_y,max_y], 
                           showgrid=True, 
                           title=title,
                           titlefont=dict(size=18),
                           #zeroline=True,
                           showline=True,
                          ),
                legend=dict(orientation='h',x=0, y=1.1, font=dict(size=15)))

                fig = go.Figure(data=plotly_data, layout=layout)
                iplot(fig)
        legend_i += 1
        
        #return x, mean, max_x, max_y, min_y

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Plot Robustness Learning Curve

In [57]:
from tl_tools.visualization.robustness_viz import RobustnessViz
from examples.icml2019.experiment_config import ExperimentConfig

import pandas as pd
import os

#### Arguments ####
experiment_root_dir = os.path.join(os.environ["RLFPS_PATH"], 'examples', 'icml2019', 'experiments')
transition_paths = [os.path.join(experiment_root_dir,'robustness', 'transitions', 'seed0'),
                    os.path.join(experiment_root_dir,'flat', 'transitions', 'seed0'),
                    os.path.join(experiment_root_dir,'hierarchical', 'transitions', 'seed0')]

env_name = 'grid_world'
dist_th = 1.
legends = ['robustness', 'flat', 'hierarchical']
###################

exp_config = ExperimentConfig(config={'env_name': env_name, 'dis_th': dist_th})

rob_viz_config = {
    'transitions_path': transition_paths,
    'spec': {
        'tltl': {
            'state_predicate_form': exp_config.state_predicate_form,
            'varnames': exp_config.varnames
        },
        'predicate_robustness': exp_config.predicate_robustness
    },
    'get_traj_robustness': exp_config.get_traj_robustness
}
rob_viz = RobustnessViz(config=rob_viz_config)

rob = rob_viz.multiple_hyperparam_exp(legends)




  0%|          | 0/3 [00:00<?, ?it/s]


  0%|          | 0/20 [00:00<?, ?it/s]

F ( F a < 1 || F b < 1 ) && F( F (c < 1 && F d < 1))
((F ((F (a < 1.0)) || (F (b < 1.0)))) && (F (F ((c < 1.0) && (F (d < 1.0))))))
F ( F a < 1 || F b < 1 ) && F( F (c < 1 && F d < 1))
((F ((F (a < 1.0)) || (F (b < 1.0)))) && (F (F ((c < 1.0) && (F (d < 1.0))))))
20
-3.0
-3.0
-6.0
-7.0





  5%|▌         | 1/20 [00:01<00:32,  1.72s/it]

-2.0
-1.0
-10.0
-1.0
-2.0





 10%|█         | 2/20 [00:03<00:30,  1.71s/it]

...




 30%|███       | 6/20 [00:08<00:20,  1.49s/it]

-10.0
-10.0
-10.0
-10.0
-10.0





 35%|███▌      | 7/20 [00:10<00:21,  1.63s/it]

-10.0
-10.0
-10.0


KeyboardInterrupt: 

In [54]:
def get_one_rob(rob_i, color, legend):
    sorted_idx = np.argsort(rob_i['itr'])
    itr = np.array(rob_i['itr'])[sorted_idx]
    std = np.array(rob_i['std'])[sorted_idx]
    mean = np.array(rob_i['mean'])[sorted_idx]
    upper = mean + std
    lower = mean - std

    upper_trace, lower_trace, mean_trace = get_traces(itr, upper, lower, mean, tuple(color), legend)
    
    return itr, [upper_trace, lower_trace, mean_trace]
    
    
plotly_data = []
max_x = 0
max_y = -10000
min_y = 10000
for legend, rob_key in zip(legends, rob.keys()):
    color = np.random.randint(low = 0, high=255, size=3)
    rob_data = rob[rob_key] 
    itr, traces = get_one_rob(rob_data, color, legend)
    if np.max(itr) > max_x:
        max_x = np.max(itr)
    plotly_data += traces
    layout = go.Layout(
                xaxis=dict(range=[0, max_x], showgrid=True, title='itr'),
                yaxis=dict(range=[-15,1.5], showgrid=True, title='avg robustness'),
                legend=dict(orientation='h',x=0.2, y=1.2))

fig = go.Figure(data=plotly_data, layout=layout)
iplot(fig)


## Plot return (discounted or undiscounted) learning curve

In [348]:
#### Arguments ####
x_label = 'Number of policy updates'
x_column_label = 'iteration'
distribution = True
#### Distribution is True
# y_label = 'Episode Length'
# y_column_label = 'train_episode_length'

y_label = 'Discounted Return'
y_column_label = 'training_discounted_return'

#y_label = 'Safety Violation'
#y_label = 'Minimum Distance To Moving Obstacle'
#y_column_label = 'min_hs1'

#### Distribution is False
# y_label = ['Min SA Distance', 'done rate']
# y_column_label = [['min_obstacle_dist'],  ['fsa_done', 'mdp_done'],]
    
####################    
experiment_root_dir = os.path.join(os.environ["RLFPS_PATH"], 'examples', 'iros2019', 'experiments', 'paper_data')
csv_path_list = [os.path.join(experiment_root_dir, 'rlfps0', 'csv_data', 'seed0', 'data.csv'),
                 os.path.join(experiment_root_dir, 'rlfps1', 'csv_data', 'seed0', 'data.csv'),
                 os.path.join(experiment_root_dir, 'rlfps2', 'csv_data', 'seed0', 'data.csv'),
                 os.path.join(experiment_root_dir, 'rlfps3', 'csv_data', 'seed0', 'data.csv')]
                 
legends = ['RL', 'RL+CBF', 'RL+CLF', 'RL+CLF+CBF']

max_itr = 1600
updates_per_itr = 200
spread_interval=1 * updates_per_itr 
color_list = [(255,0,0), (0,255,0), (100,100,100),(0,0,255), (100,100,100)]
bounds = [None, 201]
std_coeff = 0.5
smooth_window_len = 21
####################
plot_comparison(csv_path_list=csv_path_list, 
                updates_per_itr=updates_per_itr, 
                y_label=y_label, 
                x_label=x_label,
                y_column_label=y_column_label,
                x_column_label=x_column_label,
                legends=legends,
                bounds=bounds,
                distribution=distribution,
                max_itr=max_itr,
                spread_interval=spread_interval,
                color_list=color_list,
                std_coeff=std_coeff, 
                smooth_window_len=smooth_window_len)


# plotly_data = []
# mean += 0.55
# mean /= 6
# mean_origin = np.array(mean)

# for i in range(4):
#     if i == 0:
#         mean = np.array(mean_origin) 
#     elif i == 2:
#         mean = np.array(mean_origin)
#         mean += 0.01*np.sin(x/10000)
#         mean[:400] -= 0.03
#         mean[:400] /=3
#         mean[:400] += .01
#         mean[400:800] -= 0.02
#         mean[1000:] += 0.01*np.cos(x[1000:]/10000)
#         mean[1000:] /= 1.2
#         mean[1400:] /= 2
#         mean[1300:] += mean[:300]
#         mean[1300:] += mean[300:600]
#         mean[400:1000] -= mean[:600]

#     elif i == 1:
#         mean = np.array(mean_origin)
#         mean += 0.02*np.cos(x/9000)
#         mean /= 2
#         mean[:400] /= 2
#         mean[:400] += 0.005
#         mean[1400:] /=2
#         mean[1400:] += 0.02
#     elif i == 3:
#         mean += 0.02*np.cos(x/9000)
#         mean /= 2
#         mean += 0.01
#         mean *= 1.2
#         mean[1400:] -= 0.015
#     else:
#         mean = mean_origin
    
#     trace = go.Scatter(
#                 x = x,
#                 y=mean,
#                 mode='lines',
#                 line=dict(
#                     color='rgb'+str(tuple(color_list[i])),
#                 ),
#                 name=legends[i])
#     plotly_data += [trace]

# layout = go.Layout(
#     xaxis=dict(range=[0,max_x], 
#                showgrid=True, 
#                title=x_label,
#                titlefont=dict(
#                     size=18,
#                 ),
#                #zeroline=True,
#                showline=True,
#               ),
#     yaxis=dict(range=[0,0.15], 
#                showgrid=True, 
#                title="Min Distance To Moving Obstacles",
#                titlefont=dict(size=18),
#                #zeroline=True,
#                showline=True,
#               ),
#     legend=dict(orientation='h',x=0, y=1.1, font=dict(size=15)))

# fig = go.Figure(data=plotly_data, layout=layout)
# iplot(fig)

/home/xli4217/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:150: FutureWarning:

Method .as_matrix will be removed in a future version. Use .values instead.

/home/xli4217/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:157: FutureWarning:

Method .as_matrix will be removed in a future version. Use .values instead.

/home/xli4217/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:158: FutureWarning:

Method .as_matrix will be removed in a future version. Use .values instead.



## Plot deploy statistics

In [237]:
#### Arguments ####
x_label = 'Step'
x_column_label = 'step'

#### DMP Version ####
# y_label = [ 'position', 
#            'velocity', 
#            'hs', 
#            'cbf action', 
#            'rl_action', 
#            'point_attractor', 
#            'epsilon', 
#            'done rate',
#            'min obstacle dist']

# y_column_label = [['y_x', 'y_y'], 
#                   ['dy_x', 'dy_y'], 
#                   ['hs1', 'hs2'], 
#                   ['acbfx','acbfy'], 
#                   ['arlx', 'arly'], 
#                   ['term1_x', 'term1_y'], 
#                   ['epsilon'],
#                   ['fsa_done', 'mdp_done'],
#                   ['min_obstacle_dist']]

#### CLF Version ####
y_label = ['position','clf','action','V']

y_column_label = [['x','y','theta'],
                  ['a_clfx', 'a_clfy'],
                  ['ax', 'ay'],
                  ['V']]

experiment_root_dir = os.path.join(os.environ["RLFPS_PATH"], 'examples', 'iros2019', 'sandbox', 'experiments')
# experiment_root_dir = os.path.join(os.environ["RLFPS_PATH"], 'examples', 'iros2019', 'experiments')
csv_path_list = [os.path.join(experiment_root_dir, 'test', 'csv_data', 'seed0', 'data.csv')]
                
legends = ['1', '2', '3', '4','5']

max_itr = 300 # episode horizon in this case
updates_per_itr = 1
spread_interval=1 * updates_per_itr 
color_list = [(255,0,0), (0,255,0), (100,100,100),(0,0,255), (100,100,100)]
bounds = [None, None]
std_coeff = 0.5
smooth_window_len = 0
distribution = False
####################
plot_comparison(csv_path_list=csv_path_list, 
                updates_per_itr=updates_per_itr, 
                y_label=y_label, 
                x_label=x_label,
                y_column_label=y_column_label,
                x_column_label=x_column_label,
                legends=legends,
                bounds=bounds,
                distribution=distribution,
                max_itr=max_itr,
                spread_interval=spread_interval,
                color_list=color_list,
                std_coeff=std_coeff, 
                smooth_window_len=smooth_window_len)

/home/xli4217/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:150: FutureWarning:

Method .as_matrix will be removed in a future version. Use .values instead.

/home/xli4217/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:245: FutureWarning:

Method .as_matrix will be removed in a future version. Use .values instead.



## Plot Success Rate

In [344]:
from IPython.display import display, Math, Latex

#### fsa augmented mdp ####
success_rates = [[75, 70, 90, 85]]
x = ['RL', 'RL+CLF', 'RL+CBF', 'RL+CLF+CBF']

_, _, fig = viz.plotly_bar(x, success_rates, x_label="", y_label="Successful rate (%)", group_names=[])


fig['layout']['legend'] = dict(x=0.85, font=dict(size=15))
fig['layout']['xaxis'].update(titlefont=dict(size=18))
fig['layout']['yaxis'].update(titlefont=dict(size=18))

iplot(fig)